In [1]:
import os
import sys
sys.path.append(os.environ.get('NOTEBOOK_ROOT'))

import xarray as xr
import numpy as np
import pandas as pd

# Ensure string casts of NumPy arrays 
# print as much as possible (no '...').
np.set_printoptions(threshold=sys.maxsize)

import matplotlib.pyplot as plt

Matplotlib created a temporary config/cache directory at /tmp/matplotlib-vwf1269f because the default path (/home/jovyan/.config/matplotlib) is not a writable directory; it is highly recommended to set the MPLCONFIGDIR environment variable to a writable directory, in particular to speed up the import of Matplotlib and to better support multiprocessing.


In [2]:
from odc_gee.earthengine import Datacube as GEE_Datacube
dc = GEE_Datacube()

In [3]:
dc.list_products()

name                                        description  \
id                                                                           
2   ls8_l2_c1_t1_google  Landsat 8 Collection 1 Level 2 Surface Reflect...   
1   ls8_l2_c1_t2_google  Landsat 8 Collection 1 Level 2 Surface Reflect...   

    time label dataset_maturity product_family format creation_time  \
id                                                                    
2   None  None             None           None   None          None   
1   None  None             None           None   None          None   

   region_code platform   lat instrument   lon        crs  \
id                                                          
2         None     None  None       None  None  EPSG:4326   
1         None     None  None       None  None  EPSG:4326   

                               resolution tile_size     spatial_dimensions  
id                                                                          
2   (-0.00027777777778, 0.00027777777778)      None  (latitude, longitude)  
1   (-0.00027777777778, 0.00027777777778)      None  (latitude, longitude)

In [54]:
ds = dc.load(product='ls8_l2_c1_t1_google',
             # Elizabeth River, VA (sml tst)
#              lat=(36.89, 36.895),
#              lon=(-76.40,-76.395),
#              time=('2014-01-01', '2014-01-31'),
             # Elizabeth River, VA
             lat=(36.894872, 36.969353),
             lon=(-76.394949,-76.260025),
             time=('2014-01-01', '2014-06-30'),
             # Prospect Lake, CO
#              lat = (38.822297, 38.827771),
#              lon = (-104.804378, -104.793997),
             # Pueblo Reservoir, CO
#              lat = (38.23319252391589, 38.28728420493292),
#              lon = (-104.80201949531988, -104.72186163717585),
#              time=('2013-01-01', '2019-12-31'),
             measurements=['pixel_qa'],
             group_by='solar_day')

In [55]:
from utils.data_cube_utilities.clean_mask import landsat_qa_clean_mask

clean_da = \
    landsat_qa_clean_mask(ds, 'LANDSAT_8', collection='c1', level='l2')

In [56]:
import os
import uuid

import psutil

from jinja2 import Template
from IPython.display import HTML

from utils.data_cube_utilities.dc_time import _n64_to_datetime, dt_to_str

VOXEL_VIS_WEB_SVR_CMD = 'python3 server.py &'

class VoxelVisualizer():
    def _launch_server_if_not_running(self):
        # Determine if the server is running.
        process_cmds = (p.cmdline() for p in psutil.process_iter())
        cmd_found = False
        for cmd in process_cmds:
            for token in VOXEL_VIS_WEB_SVR_CMD.split():
                if token != '&' and token not in cmd:
                    break
                cmd_found = True
                break
            if cmd_found:
                break
        # If the server is not running, start it.
        if not cmd_found:
            os.system(VOXEL_VIS_WEB_SVR_CMD)
    
    def __init__(self):
        self.id = uuid.uuid4()
        # Launch the webserver.    
        self._launch_server_if_not_running()
        fs = open('template.html','r')
        self.template = Template(fs.read())
        fs.close()
    
    def draw(self, da: xr.DataArray):
        if not da.dtype == 'bool':
            raise Exception("You need to pass a boolean xarray.DataArray to use this.")
        
        # Reverse the x dimension.
        da = da.sel(longitude=da.longitude[::-1]).astype(np.int8)
        
        da_str = str(da.values.tolist())#.replace('array(', '').replace(')', '')#.replace('\n', ',').replace(',,', ',')
        times_str = str([dt_to_str(_n64_to_datetime(time), fmt='%Y-%m-%dT%H:%M:%S.%f') 
                         for time in clean_da.time.values]).replace(',', ',\n')
        # Render the template and ensure the 
        # HTML is all on one line for the iframe.
#         print(f'base_template: {self.template.render(data_array=da_str, times=times_str)}')
        filled_template = self.template.render(data_array=da_str, times=times_str)
#         print(filled_template)
#         print()
        
        # Remove single line comments and add 
        # line continuation characters (\ in JS).
        filled_template_no_sngl_lne_cmts = []
        for i, line in enumerate(filled_template.splitlines()):
#             if 100 < i and i < 200:
#                 print(i, line)
            import re
#             line = re.sub(r'\b//.*', r'', line)
#             if not line.startswith('//'):
            if re.search('^\s*//', line) is None:
                filled_template_no_sngl_lne_cmts.append(line)
#             else:
#                 print(i, line)
#         filled_template_no_sngl_lne_cmts = '\\\n'.join(filled_template_no_sngl_lne_cmts)#.replace('\n', '\\\n')
        filled_template_sngl_lne = ''.join(filled_template_no_sngl_lne_cmts)
#         print(filled_template_sngl_lne[:1000])
        
        # Escape quotes for JS string concatenation.
        filled_template_sngl_lne_esc = filled_template_sngl_lne\
            .replace('\"', '\\"').replace("\'", "\\'")#\
            #.replace('<', '\<').replace('>', '\>')
            #.replace('\n', '\\n')
#         print(filled_template_sngl_lne_esc[:1000])
        # Escape angle brackets for elements.
#         filled_template_esc = re.sub(r'<(.*)>', r'\<\1\>', filled_template_esc)
#         print(filled_template_esc)
#         print(f"{filled_template_esc[:1000]}")
        
        # "Escape" script tags to avoid closing the script tag
        # containing the substituted filled template HTML string.
        end_scr = '/script>'
        filled_template_sngl_lne_esc_split = \
            re.split(end_scr, filled_template_sngl_lne_esc)
#         filled_template_sngl_lne_esc_split_fmt = \
#             [f"\"{string}\"" for string in filled_template_sngl_lne_esc_split]
#         filled_template_sngl_lne_esc_fmt = \
#             " + \'/script>\'".join(filled_template_sngl_lne_esc_split_fmt)
        # Format the strings to form the full string in JS by concat.
        filled_template_sngl_lne_esc_split_fmt = []
        for i, string in enumerate(filled_template_sngl_lne_esc_split):
            # All but first must have end script tag restored.
            # All are enclosed in single quotes.
            if i > 0:
                string = f"\'{end_scr}{string}\'"
            else:
                string = f"\'{string}\'"
            filled_template_sngl_lne_esc_split_fmt.append(string)
        filled_template_sngl_lne_esc_fmt = \
            " + ".join(filled_template_sngl_lne_esc_split_fmt)

#         with open('tst.txt', 'w') as file:
#             file.write(filled_template_sngl_lne_esc_fmt)
    
#         import html
#         filled_template_esc = html.escape(filled_template_esc)
#         print(filled_template_esc)
#         out_file = f'out{self.id}.html'
#         self.save(filled_template, out_file)
        vox_vis_server_port = os.environ['VOXEL_VISUALIZER_PORT']
        self.iframe = HTML(f"""
        <iframe id='iframe', sandbox='allow-same-origin allow-scripts', width=600, height=350></iframe>
        <script>
          var hostname = window.location.hostname;
          var static_url = 'http://' + hostname + ':{vox_vis_server_port}/static';
          console.log("static_url " + static_url);
          var srcdoc = {filled_template_sngl_lne_esc_fmt}; """ + """
          // console.log("srcdoc " + srcdoc);
          srcdoc = srcdoc.replaceAll('static_url', static_url);
          console.log("srcdoc " + srcdoc);
          // console.log(url2);
          document.getElementById('iframe').srcdoc = srcdoc;
          // doc = document.getElementById('iframe').contentWindow.document;
          // doc.open();
          // doc.write(url2);
          // doc.write('<html><head><title></title></head><body><h1>Hello world.</h1></body></html>');
          // url2
          // doc.close();
        </script>
        """)
#         // var url1 = 'http://' + hostname + ':{vox_vis_server_port}/static/{out_file}';
#         var srcdoc = "{filled_template_sngl_lne_esc}".replace('\{\{ static_url \}\}', static_url)
        
#         """<iframe id='iframe' srcdoc="{filled_template_sngl_lne}" width=600 height=350 sandbox='allow-same-origin allow-scripts'></iframe>"""
#         """
#         <script>
#           // var hostname = window.location.hostname;
#           // var url1 = 'http://' + hostname + ':{vox_vis_server_port}/static/{out_file}';
#           // console.log(url2);
#           // document.getElementById('iframe').srcdoc = url2;
#           // doc = document.getElementById('iframe').contentWindow.document;
#           // doc.open();
#           // doc.write(url2);
#           // doc.write('<html><head><title></title></head><body><h1>Hello world.</h1></body></html>');
#           // url2
#           // doc.close();
#         </script>
#         """
#         var url = f'data:text/html,escape("{filled_template}")'
#         var url2 = 'data:text/html;charset=utf-8,' + escape("{filled_template_esc}");
#         var url2 = "{filled_template_esc}";
#         print()    
#         print(f"""
#         <iframe id='iframe', sandbox='allow-same-origin allow-scripts', width=600, height=350></iframe>
#         <script>
#           var hostname = window.location.hostname;
#           var url = 'http://' + hostname + ':{vox_vis_server_port}/static/{out_file}'
#           var url2 = 'data:text/html,' + escape("{filled_template_esc}")
#           console.log(url);
#           document.getElementById('iframe').src = url;
#         </script>"""[-10000:])
        return self.iframe

    def save(self, data, location):
        fs = open(location, "w")
        fs.write(data)
        fs.close()
        return 

In [57]:
# def voxel_vis(da: xr.DataArray, )

In [58]:
voxel_visualizer = VoxelVisualizer()

In [59]:
voxel_visualizer.draw(clean_da)

In [10]:
# (ds.pixel_qa == 1).mean('time').plot()

In [11]:
# ds.pixel_qa.median('time').plot()

In [12]:
# clean_da.mean('time').plot()